In [1]:
import pandas as pd
import re
from collections import Counter
pd.options.mode.chained_assignment = None  # default='warn'
from sklearn.preprocessing import MultiLabelBinarizer

In [2]:
def assignDivision(divisionsDict, divisions):
    for key in divisionsDict:
        div = re.split(r' |/|\+|,|-', divisionsDict[key])
        for d in divisions: #loop through list with known divisions
            if d in div:
                assignedDiv = d
                break
        divisionDict[key] = {'Assigned division': assignedDiv}
    return divisionDict

In [3]:
#load 
researchers = pd.read_pickle("Files/Dataframes/researchers_wGender.pkl")
researchers['SponsoringUnit'] = researchers.SponsoringUnit.fillna('Unknown')

In [4]:
#APS Units
sponsorFile = open("Files/sponsoringUnits.txt", "r").read()
sponsorList = sponsorFile.replace('\n', ';').split(';')
sponsor_abr = re.findall(r'\((.*)\)', sponsorFile) #abbreviations for the sponsoring units
sponsorNames = re.findall(r'(.*) \(', sponsorFile) #ful name of sponsoring unit

In [5]:
researchers['AllSponsoringUnits'] = researchers.SponsoringUnit.str.split(r' |/|\+|,|-')
researcher_SponsoringUnits = researchers.explode('AllSponsoringUnits') 

In [6]:
#df with only divisions known from the APS homepage
researcher_knownDivisions = researcher_SponsoringUnits[researcher_SponsoringUnits.AllSponsoringUnits.isin(sponsor_abr)].reset_index(drop = True)

In [7]:
sponsorDict = dict(zip(sponsor_abr, sponsorNames))

In [8]:
researcher_knownDivisions['AssignedSponsoringUnit'] = researcher_knownDivisions['AllSponsoringUnits'].apply(lambda x: sponsorDict.get(x))
#researcher_knownDivisions['AssignedSponsoringUnit'] = researcher_knownDivisions['SponsoringUnit'].apply(lambda x: sponsorDict.get(x))

In [9]:
#remove sponsoring units column with abbreviations
researcher_knownDivisions = researcher_knownDivisions.drop('AllSponsoringUnits', axis = 1)

In [10]:
researcher_knownDivisions.to_pickle("Files/Dataframes/researchersFinal.pkl") 

## One-hot encoding of sponsoring units

In [11]:
#intersection of divisions in data and from APS site on units
knownDivisions = list(set(sponsor_abr).intersection(set(researcher_SponsoringUnits.AllSponsoringUnits.unique())))

In [12]:
mlb = MultiLabelBinarizer(sparse_output=True)

oneHot = researchers.join(pd.DataFrame.sparse.from_spmatrix(
    mlb.fit_transform(researchers.pop('AllSponsoringUnits')),
    index = researchers.index, 
    columns = mlb.classes_))

In [52]:
#Select columns
cols = list(researchers.columns)
cols += knownDivisions 

In [55]:
#df with researcher with one-hot encoded sponsoring units
oneHot_researchers = oneHot[cols]

In [56]:
#save one-hot encoding df
oneHot_researchers.to_pickle("Files/Dataframes/researchers_oneHot.pkl") 

In [11]:
def mostOccurentUnit(df, unique_df): #df is with all researchers and their data, unique_df is unique wrt. name and year
    for i in unique_df.index:
        current = unique_df[unique_df.index == i]
        name = current.SearchName
        year = current.Year
        result = df[(df.Year == year) & (df.SearchName == name)]
        print(result)

In [20]:
researcher_knownDivisions.iloc[9]

ID                                                                   155013
SearchName                                                       owen lewis
FirstName                                                              owen
AuthorCount                                                              81
MaxPaperCount                                                            23
API_Field                                                          Medicine
API_FieldCount                                                            9
ExternalField                                                      Medicine
ModelField                                                          Biology
ExternalFieldCount                                                        9
ModelFieldCount                                                          11
FirstPaperYear                                                         2005
Year                                                                   2021
Name        

In [13]:

test = researcher_knownDivisions[(researcher_knownDivisions.SearchName == 'owen lewis') & (researcher_knownDivisions.Year <= 2021)]
#test.groupby('AssignedSponsoringUnit').count()
test
#'AssignedSponsoringUnit'].values

ID  SearchName FirstName  AuthorCount  MaxPaperCount API_Field  \
9   155013  owen lewis      owen           81             23  Medicine   
10  155013  owen lewis      owen           81             23  Medicine   
11  155013  owen lewis      owen           81             23  Medicine   
12  155013  owen lewis      owen           81             23  Medicine   

    API_FieldCount ExternalField ModelField  ExternalFieldCount  ...  \
9                9      Medicine    Biology                   9  ...   
10               9      Medicine    Biology                   9  ...   
11               9      Medicine    Biology                   9  ...   
12               9      Medicine    Biology                   9  ...   

                                                Title         SponsoringUnit  \
9   Systematic investigation of a two-fluid model ...  DBIO DPOLY GSNP DSOFT   
10  Systematic investigation of a two-fluid model ...  DBIO DPOLY GSNP DSOFT   
11  Systematic investigation of a two-fluid model ...  DBIO DPOLY GSNP DSOFT   
12  Systematic investigation of a two-fluid model ...  DBIO DPOLY GSNP DSOFT   

    SessionIndex SessionType Seniority  CumulativePaperCount Productivity  \
9       127340.0    attendee        16                    16          1.0   
10      127340.0    attendee        16                    16          1.0   
11      127340.0    attendee        16                    16          1.0   
12      127340.0    attendee        16                    16          1.0   

   firstName  Gender AssignedSponsoringUnit  
9       owen       M                   None  
10      owen       M                   None  
11      owen       M                   None  
12      owen       M                   None  

[4 rows x 26 columns]

In [14]:
researcher_knownDivisions[researcher_knownDivisions.SearchName == 'satish kumar thittamaranahalli'].Year

599400    2020
599401    2020
Name: Year, dtype: int64

In [68]:
unique = researchers.drop_duplicates(subset = ['SearchName', 'Year'])

In [32]:
mostOccurentUnit(researchers, unique)

       ID  SearchName FirstName  AuthorCount  MaxPaperCount    API_Field  \
0  155001  niels john     niels            6              7  Mathematics   

   API_FieldCount ExternalField   ModelField  ExternalFieldCount  ...  \
0               2   Mathematics  Mathematics                   2  ...   

   AuthorIndex                                              Title  \
0          3.0  Robustness of Helical Edge States Under Edge R...   

   SponsoringUnit SessionIndex SessionType  Seniority CumulativePaperCount  \
0            None     127314.0    attendee         12                    7   

  Productivity  firstName Gender  
0     0.583333      niels      M  

[1 rows x 25 columns]
       ID  SearchName FirstName  AuthorCount  MaxPaperCount    API_Field  \
1  155001  niels john     niels            6              7  Mathematics   

   API_FieldCount ExternalField   ModelField  ExternalFieldCount  ...  \
1               2   Mathematics  Mathematics                   2  ...   

   AuthorIn

         ID       SearchName  FirstName  AuthorCount  MaxPaperCount  \
105  155103  francesco preti  francesco            2             17   

             API_Field  API_FieldCount      ExternalField   ModelField  \
105  Materials Science               8  Materials Science  Engineering   

     ExternalFieldCount  ...  AuthorIndex  \
105                   8  ...          1.0   

                                                 Title  SponsoringUnit  \
105  Continuous Quantum Gate Sets and Pulse-Class M...             DQI   

    SessionIndex SessionType  Seniority CumulativePaperCount Productivity  \
105     127454.0    attendee          5                   16          3.2   

     firstName Gender  
105  francesco      M  

[1 rows x 25 columns]
         ID      SearchName FirstName  AuthorCount  MaxPaperCount   API_Field  \
106  155104  anna j. miller      anna            6              2  Psychology   

     API_FieldCount ExternalField ModelField  ExternalFieldCount  ...  \
106   

         ID      SearchName FirstName  AuthorCount  MaxPaperCount  \
224  155215  masahiro toiya  masahiro            1             18   

             API_Field  API_FieldCount      ExternalField ModelField  \
224  Materials Science              11  Materials Science    Physics   

     ExternalFieldCount  ...  AuthorIndex                             Title  \
224                  11  ...          1.0  Shear reversal in granular flows   

     SponsoringUnit SessionIndex SessionType  Seniority CumulativePaperCount  \
224             DFD     127589.0    attendee          2                    4   

    Productivity  firstName Gender  
224          2.0   masahiro      M  

[1 rows x 25 columns]
         ID            SearchName FirstName  AuthorCount  MaxPaperCount  \
235  155220  juan ignacio beltran      juan            1             38   

             API_Field  API_FieldCount      ExternalField         ModelField  \
235  Materials Science              19  Materials Science  Materials

         ID      SearchName FirstName  AuthorCount  MaxPaperCount  \
359  155337  thomas a baran    thomas            1             25   

            API_Field  API_FieldCount     ExternalField        ModelField  \
359  Computer Science              22  Computer Science  Computer Science   

     ExternalFieldCount  ...  AuthorIndex  \
359                  22  ...          6.0   

                                                 Title  SponsoringUnit  \
359  Signal Processing Perspectives on Pulse Design...             DQI   

    SessionIndex SessionType  Seniority CumulativePaperCount Productivity  \
359     127735.0    attendee         20                   25         1.25   

     firstName Gender  
359     thomas      M  

[1 rows x 25 columns]
         ID   SearchName FirstName  AuthorCount  MaxPaperCount  \
360  155338  sascha preu    sascha            7            209   

             API_Field  API_FieldCount      ExternalField ModelField  \
360  Materials Science             

         ID      SearchName FirstName  AuthorCount  MaxPaperCount API_Field  \
466  155447  yosef yeshurun     yosef            6              4   Physics   

     API_FieldCount ExternalField ModelField  ExternalFieldCount  ...  \
466               2       Physics    Physics                   2  ...   

     AuthorIndex                                              Title  \
466          3.0  Large oscillations of the magnetoresistance in...   

     SponsoringUnit SessionIndex SessionType  Seniority CumulativePaperCount  \
466            DCMP     127894.0    attendee         23                    4   

    Productivity  firstName Gender  
466     0.173913      yosef      M  

[1 rows x 25 columns]
         ID          SearchName FirstName  AuthorCount  MaxPaperCount  \
467  155448  zahra shafieizadeh     zahra            1             13   

             API_Field  API_FieldCount      ExternalField ModelField  \
467  Materials Science              10  Materials Science    Physics   

 

...

          ID    SearchName FirstName  AuthorCount  MaxPaperCount API_Field  \
9570  147627  felix zeides     felix            2              1   Physics   

      API_FieldCount ExternalField   ModelField  ExternalFieldCount  ...  \
9570               1       Physics  Engineering                   1  ...   

      AuthorIndex                                              Title  \
9570          5.0  Characterizing and manipulating two level defe...   

      SponsoringUnit SessionIndex SessionType  Seniority CumulativePaperCount  \
9570             GQI     117355.0    attendee         -7                    0   

     Productivity  firstName Gender  
9570         -0.0      felix      M  

[1 rows x 25 columns]
          ID  SearchName FirstName  AuthorCount  MaxPaperCount API_Field  \
9574  147632  ali abboud       ali           20             14  Medicine   

      API_FieldCount ExternalField ModelField  ExternalFieldCount  ...  \
9574              10      Medicine    Unknown           

          ID          SearchName FirstName  AuthorCount  MaxPaperCount  \
9672  147712  gustavo a. narvaez   gustavo            2             34   

     API_Field  API_FieldCount ExternalField ModelField  ExternalFieldCount  \
9672   Physics              22       Physics    Physics                  22   

      ...  AuthorIndex                                              Title  \
9672  ...          1.0  Shape, charge, and alloy fluctuation effects o...   

      SponsoringUnit SessionIndex SessionType  Seniority CumulativePaperCount  \
9672            FIAP     117450.0    attendee          9                   17   

     Productivity  firstName Gender  
9672     1.888889    gustavo      M  

[1 rows x 25 columns]
          ID          SearchName FirstName  AuthorCount  MaxPaperCount  \
9673  147712  gustavo a. narvaez   gustavo            2             34   

     API_Field  API_FieldCount ExternalField ModelField  ExternalFieldCount  \
9673   Physics              22       Physics   

          ID     SearchName FirstName  AuthorCount  MaxPaperCount  \
9772  147804  volker hoeink    volker            2              2   

              API_Field  API_FieldCount      ExternalField ModelField  \
9772  Materials Science               1  Materials Science    Physics   

      ExternalFieldCount  ...  AuthorIndex  \
9772                   1  ...          2.0   

                                                  Title  SponsoringUnit  \
9772  Magnetic Tunnel Junctions (MTJ) with Large Tun...        DMP GMAG   

     SessionIndex SessionType  Seniority CumulativePaperCount Productivity  \
9772     117596.0    attendee          2                    1          0.5   

      firstName Gender  
9772     volker      M  

[1 rows x 25 columns]
          ID    SearchName FirstName  AuthorCount  MaxPaperCount  \
9773  147805  weifeng shen   weifeng           35            112   

              API_Field  API_FieldCount      ExternalField   ModelField  \
9773  Materials Science     

          ID         SearchName FirstName  AuthorCount  MaxPaperCount  \
9869  147881  alex taekyung lee      alex            5              2   

              API_Field  API_FieldCount      ExternalField ModelField  \
9869  Materials Science               1  Materials Science    Unknown   

      ExternalFieldCount  ...  AuthorIndex  \
9869                   1  ...          1.0   

                                                  Title  SponsoringUnit  \
9869  The effect of carbon vacancies on the electric...             DMP   

     SessionIndex SessionType  Seniority CumulativePaperCount Productivity  \
9869     137486.0    attendee         -3                    0         -0.0   

      firstName Gender  
9869       alex      M  

[1 rows x 25 columns]
          ID         SearchName FirstName  AuthorCount  MaxPaperCount  \
9870  147881  alex taekyung lee      alex            5              2   

              API_Field  API_FieldCount      ExternalField ModelField  \
9870  Materi


KeyboardInterrupt



In [ ]:
#create df with the most occurent sponsoring unit at the time of the conference, so based on Year and name.
#This is based on unique wrt. Year and Name